In [4]:
from pynq import PL
PL.reset() #important fixes caching issues which have popped up.
import xrfdc #poorly documented library that handles interfacing to the RF data converter
from pynq import Overlay  #import the overlay module
ol = Overlay('./adsb_decoder_lowpass.bit')  #locate/point to the bit file
import pprint
pprint.pprint(ol.ip_dict)
dma = ol.real_dma #might need to change name depending on what you called it
rf = ol.usp_rf_data_converter_0 #might need to change name depending on what you called it
from pynq import Clocks
Clocks.pl_clk0_mhz = 150
print(Clocks.pl_clk0_mhz)

print(rf)

{'real_dma': {'addr_range': 65536,
              'bdtype': None,
              'device': <pynq.pl_server.embedded_device.EmbeddedDevice object at 0xffffb7966530>,
              'driver': <class 'pynq.lib.dma.DMA'>,
              'fullpath': 'real_dma',
              'gpio': {},
              'interrupts': {},
              'mem_id': 'S_AXI_LITE',
              'memtype': 'REGISTER',
              'parameters': {'ADDR_WIDTH': '10',
                             'ARUSER_WIDTH': '0',
                             'AWUSER_WIDTH': '0',
                             'BUSER_WIDTH': '0',
                             'CLK_DOMAIN': 'design_1_zynq_ultra_ps_e_0_0_pl_clk0',
                             'C_BASEADDR': '0xA0000000',
                             'C_DLYTMR_RESOLUTION': '125',
                             'C_ENABLE_MULTI_CHANNEL': '0',
                             'C_FAMILY': 'zynquplus',
                             'C_HIGHADDR': '0xA000FFFF',
                             'C_INCLUDE_MM2S':

                                                                                  'Decode '
                                                                                  'Errors.      '
                                                                                  '1 '
                                                                                  '- '
                                                                                  'SG '
                                                                                  'Decode '
                                                                                  'Error '
                                                                                  'detected. '
                                                                                  'DMA '
                                                                                  'Engine '
                                                                                  'halts.

                                            'DAC_Mixer_Type30': '3',
                                            'DAC_Mixer_Type31': '3',
                                            'DAC_Mixer_Type32': '3',
                                            'DAC_Mixer_Type33': '3',
                                            'DAC_Mode00': '0',
                                            'DAC_Mode01': '0',
                                            'DAC_Mode02': '0',
                                            'DAC_Mode03': '0',
                                            'DAC_Mode10': '0',
                                            'DAC_Mode11': '0',
                                            'DAC_Mode12': '0',
                                            'DAC_Mode13': '0',
                                            'DAC_Mode20': '0',
                                            'DAC_Mode21': '0',
                                            'DAC_Mode22': '0',
                               

                                      'PSU__GEN_IPI_6__MASTER': 'PMU',
                                      'PSU__GEN_IPI_7__MASTER': 'NONE',
                                      'PSU__GEN_IPI_8__MASTER': 'NONE',
                                      'PSU__GEN_IPI_9__MASTER': 'NONE',
                                      'PSU__GEN_IPI__TRUSTZONE': '<Select>',
                                      'PSU__GPIO0_MIO__IO': '<Select>',
                                      'PSU__GPIO0_MIO__PERIPHERAL__ENABLE': '0',
                                      'PSU__GPIO1_MIO__IO': '<Select>',
                                      'PSU__GPIO1_MIO__PERIPHERAL__ENABLE': '0',
                                      'PSU__GPIO2_MIO__IO': '<Select>',
                                      'PSU__GPIO2_MIO__PERIPHERAL__ENABLE': '0',
                                      'PSU__GPIO_EMIO_WIDTH': '1',
                                      'PSU__GPIO_EMIO__PERIPHERAL__ENABLE': '0',
                             

In [5]:
adc_tile = rf.adc_tiles[2]
print(adc_tile)
adc_block = adc_tile.blocks[0]
print(adc_block)
print(adc_block.BlockStatus)
print(adc_block.MixerSettings)
adc_block.Dither = 0 #doesn't really matter for this lab, but let's turn off.
center_frequency = 1090
adc_block.MixerSettings['Freq']= center_frequency # set the frequency of the Numerically controlled oscillator.
adc_block.UpdateEvent(xrfdc.EVENT_MIXER) #every time setting is changed, must call this.
print(adc_block.MixerSettings)

{'SamplingFreq': 1.024, 'AnalogDataPathStatus': 1, 'DigitalDataPathStatus': 769, 'DataPathClocksStatus': 1, 'IsFIFOFlagsEnabled': 3, 'IsFIFOFlagsAsserted': 0}
{'Freq': 0.0, 'PhaseOffset': 0.0, 'EventSource': 2, 'CoarseMixFreq': 16, 'MixerMode': 3, 'FineMixerScale': 0, 'MixerType': 2}
{'Freq': 1090.0, 'PhaseOffset': 0.0, 'EventSource': 2, 'CoarseMixFreq': 0, 'MixerMode': 3, 'FineMixerScale': 0, 'MixerType': 2}


In [6]:
import numpy as np
import time
import pyModeS as pms
%matplotlib notebook
import matplotlib.pyplot as plt
from pynq import allocate

out_buffer = allocate(128 // 8, dtype=np.uint8)

while True:
    # Trigger the DMA transfer and wait for the result
    dma.recvchannel.transfer(out_buffer)
    dma.recvchannel.wait()

    raw_squitter_data = ""
    for b in out_buffer[0:14]:
        raw_squitter_data = f"{b:02x}" + raw_squitter_data
    #print(raw_squitter_data)
    #pms.tell(raw_squitter_data)
    if pms.df(raw_squitter_data) == 17 and pms.crc(raw_squitter_data) == 0:
        pms.tell(raw_squitter_data)
        print(raw_squitter_data)
        print()

                     Message: 8da38af8990c459d885c06d3e05c 
                ICAO address: a38af8 
             Downlink Format: 17 
                    Protocol: Mode-S Extended Squitter (ADS-B) 
                        Type: Airborne velocity 
                       Speed: 244 knots
                       Track: 196.13841857163405 degrees
               Vertical rate: -1408 feet/minute
                        Type: Ground speed 
8da38af8990c459d885c06d3e05c

                     Message: 8da38af8582987c2870f3718af3a 
                ICAO address: a38af8 
             Downlink Format: 17 
                    Protocol: Mode-S Extended Squitter (ADS-B) 
                        Type: Airborne position (with barometric altitude) 
                  CPR format: Odd 
                CPR Latitude: 0.9399642944335938 
               CPR Longitude: 0.5297164916992188 
                    Altitude: 7200 feet
8da38af8582987c2870f3718af3a

                     Message: 8dac95165907a03f94a1702232aa 

Exception ignored in: <function PynqBuffer.__del__ at 0xffff83c36440>
Traceback (most recent call last):
  File "/usr/local/share/pynq-venv/lib/python3.10/site-packages/pynq/buffer.py", line 62, in __del__
    def __del__(self):
KeyboardInterrupt: 


KeyboardInterrupt: 